In [ ]:
# General imports for data handling, data analysis, and plotting

import numpy as np
import os
from astropy.coordinates import Angle
from astropy import units as u

import matplotlib as mpl
import matplotlib.pyplot as plt

# Setting the rcParams is an easy way of fixing some 
# plotting settings at the very beginning
mpl.rcParams['lines.linewidth'] = 2.5
mpl.rcParams['font.size'] = 20

In [ ]:
# Download the events from
# https://icecube.wisc.edu/data-releases/2022/11/evidence-for-neutrino-emission-from-the-nearby-active-galaxy-ngc-1068/
# The .txt file containing the reconstructed observables of the experimental data is /resources/event_list.txt

events_file = '/Users/chiarabellenghi/Downloads/ps_data_release/resources/event_list.txt'

In [ ]:
# numpy offert an easy to use method to load and parse the columns in a text file
# (doesn't have to be a .txt, can be a .csv too, for example. Or whatever text file).
# Let's look at how it works:
np.loadtxt?

In [ ]:
# Load the experimental data with numpy!
# We are mainly interested in the spatial coordinates of the events
# for this exercise.

'...'

In [ ]:
# Convert the coordinates in degrees
'...'

In [ ]:
# We know the position of NGC 1068 from the astronomical catalogs!
# For example, we can look it up in SIMBAD: an astronomical database that 
# provides basic data, cross-identifications, bibliography, and measurements
# for astronomical objects outside the solar system.

ngc_ra = '2h42m40.7091669408s'
ngc_dec = '-0d00m47.859690204s'

ngc_ra_deg, ngc_dec_deg = Angle(ngc_ra).deg, Angle(ngc_dec).deg
print(f"NGC 1068 is located at (R.A., Dec.) = ({ngc_ra_deg}, {ngc_dec_deg}) degrees.")

In [ ]:
# Now we can calculate the angular distance of each event from the source
# Let's define a function that can do that!

def GreatCircleDistance(ra_1, dec_1, ra_2, dec_2):
    r"""Compute the great circle distance between points in the sky.
    All coordinates must be given in degrees.
    """

    # Convert all coordinates to radians
    ra1 = np.deg2rad(ra_1)
    dec1 = np.deg2rad(dec_1)
    ra2 = np.deg2rad(ra_2)
    dec2 = np.deg2rad(dec_2)
    
    delta_dec = np.abs(dec1 - dec2)
    delta_ra = np.abs(ra1 - ra2)
    x = (np.sin(delta_dec / 2.0)) ** 2.0 + np.cos(dec1) * np.cos(dec2) * (
        np.sin(delta_ra / 2.0)
    ) ** 2.0
    return np.rad2deg(2.0 * np.arcsin(np.sqrt(x)))

In [ ]:
# Calculate the square angular distance from the source for all events in the sample
psi_square = '...'

# Then let's limit our analysis to events that have psi_square <= 6
'...'

In [ ]:
# Let's make a histogram out of our data!
# We can use np.histogram for this too. Remember to compute also
# poisson errors on the counts!

bins = np.arange(0, 6.0, 0.33)
centers = '...'
bin_width = '...'
counts_exp = '...'
errs_exp = '...'

In [ ]:
# Let's plot our histogram!

fig, ax = plt.subplots()
'...'

ax.set_ylabel(r"Events", labelpad=15)
ax.set_xlabel(r"$\hat{\psi}^2$ [deg$^2$]", labelpad=12)

plt.title('All data within $\psi^2=6$ deg$^2$', fontsize=18)

In [ ]:
# Given the angular resolution of the IceCube detector, we know
# that on average the lowest energy events (100GeV) are reconstructed
# not further than 2 degrees away from the parent neutrino direction.
# We can estimate the background counts from region where psi_square > 3
control_region = '...'

# Let's plot the masked data in a new histogram now!
fig, ax = plt.subplots()
'...'

ax.set_ylabel(r"Events", labelpad=15)
ax.set_xlabel(r"$\hat{\psi}^2$ [deg$^2$]", labelpad=12)

plt.title('Control Region for Bkg Estimation', fontsize=18)

In [ ]:
# Our expectation is that in the psi^2 space (which is uniform in declination),
# the background should be uniform. So we could try to fit a uniform distribution
# to the data in our control region.

# We can try two different fitting methods and check for the differences to
# decide which one works best for us.

from scipy.stats import uniform
from scipy.optimize import curve_fit

mask_ctrl_region = psi_square > 3

# First fitting method:
#`fit` method from the scipy.stats.uniform object.
# The default estimation method for the fit parameters is the Maximum
# Mikelihood Estimation (MLE).
fit_params = uniform.fit('...')
print("Result from the MLE in scipy.stats: ", uniform.pdf(centers[-1], *fit_params)*psi_square[mask_ctrl_region].size*bin_width[-1])

# Second method:
# `curve_fit method` from the scipy.optimize module.
# Use non-linear least squares to fit a function, f, to data.
# One advantage is that we get an estimate of the covariance matrix too,
# which gives us an estimate for the errors on the fit parameter
def func('...'):
    return '...'
popt, pcov = curve_fit('...')
print("Result from the curve_fit in scipy.optimize: ", popt, pcov)

In [ ]:
# Plot again the control region with the 2 estimates for the background expectation!

fig, ax = plt.subplots()
'...'

ax.set_ylabel(r"Events", labelpad=15)
ax.set_xlabel(r"$\hat{\psi}^2$ [deg$^2$]", labelpad=12)

plt.title('Control Region for Bkg Estimation', fontsize=18)

# BAD SCIENTIFIC PRACTICE

What did I do? I checked on my own experimental data the performances of two different analyses method.
#### By doing that, I biased myself!
Now, of course, I want to use the method that gives me the lower estimate for the background because that's the one that will probably give me a more significant result for my excess.

This is why it is **extremely important** to always define your analysis strategy blindly, before looking at your experimental data. In IceCube we develop and prepare all the details about our analyses on simulations. Only once we are completely sure of what methods and procedures we want to use, we finally look at the data

In [ ]:
# Well, now it's too late and I am biased. Let's use the curve_fit result,
# which also gives us an estimate on the error on the fit parameter :)

background_counts_per_bin = popt[0]

# Estimate the significance of the effect

We can use a simple chi-square test-statistic.

$\chi^2 = \sum{\frac{(O_i-E_i)^2}{E_i}}$

It's basically a measurement of how much the observations $O$ in each bin $i$ deviates from the expectations $E$.

In [ ]:
# Let's compute the residuals squared
# We need to look at the region of interest for the signal
# So now we limit ourselves to bins where psi_square <=3

mask_roi = '...'

In [ ]:
def chisquare_func('...'):
    r"""Computes the chi square test-statistic (TS)
    value given the expectation and the observation.
    
    Parameters
    ----------


    Returns
    -------

    """
        
    chi_square = '...'
    
    return chi_square

In [ ]:
chi_square = chisquare_func('...')
chi_square

In [ ]:
# We can use the chi2 distribution to compute the probability of obtaining 
# a result more extreme than the one that we obtained when only background
# is producing our data fluctuations!

from scipy.stats import chi2

# The number of degrees of freedom for this test is the number of bins we
# are using in our region of interest (ROI)
p_value = chi2.sf('...')
print(f'The probability of getting a chi-square of {chi_square:2f} from random fluctuations is {p_value:1.1e}.')

In [ ]:
from scipy.special import erfinv

def pval2Sigma(pval):
    r"""Converts p-values into Gaussian sigmas.
    Parameters
    ----------
    pval : float or array_like
        p-values to be converted in Gaussian sigmas
    Returns
    -------
    ndarray
        Gaussian sigma values
    """
    return np.sqrt(2)*erfinv(1-2*pval)

In [ ]:
print(f"We can convert the p-value that we obtained into a number of Gaussian-equivalent sigmas: {pval2Sigma(p_value):.1f} sigma.")

### So, why didn't we get the 4.2$\sigma$ published by the IceCube collaboration?

Well, the analyses we perform in IceCube are a bit more sophisticated and take into account more information about the single event reconstruction: We include in our statistical test (a so-called likelihood-ratio-test) information about the quality of the directional reconstruction of the event and about the reconstructed muon energy.

But seeing a relatively interesting excess even by simply doing a very minimal 1D binned spatial analysis probably makes this result even more credible :)

In [ ]:
# Plot the total histogram with the background expectation

fig, ax = plt.subplots()
'...'

plt.title('All data within $\psi^2=6$ deg$^2$ w/ bkg expectation', fontsize=18)